# Configure KBase Jupyter Dev Environment

In [1]:
%run cliffcommutil.py
logger = logging.getLogger(__name__)
logger.setLevel(logging.INFO)

python version 3.9.13
KBBaseModules 0.0.1


1710441292.5897129 INFO: Note: NumExpr detected 16 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
1710441292.5903769 INFO: NumExpr defaulting to 8 threads.


modelseedpy 0.3.3
cobrakbase 0.3.1
Output files printed to:/Users/chenry/workspace/Notebooks//ProbComm//sessions/default/output when using KBDevUtils.output_dir


# Important links
* https://github.com/ModelSEED/MicrobiomeNotebooks.git
* MAG files: /home/fliu/cliff_mags/data/ : annotation_ani_prob_gep_85.json / annotation_ani_prob_lo_85.json

# Gathering hits from data file and establishing thresholds to use

In [17]:
%run cliffcommutil.py
#data = json.load(open('data/annotation_ani_prob_gep_85.json'))
data = json.load(open('/home/fliu/cliff_mags/data/annotation_ani_prob_lo_85.json'))
mag_ani_data = {}
mag_thresholds = {}
mag_hit_distribution = {}
for function in data.keys():
    for mag in data[function].keys():
        if mag not in mag_ani_data:
            mag_ani_data[mag] = {}
            mag_hit_distribution[mag] = [0] * 21
        for hit in data[function][mag].keys():
            genome = hit.split(":")[0]
            if data[function][mag][hit] < 100:
                if genome not in mag_ani_data[mag]:
                    mag_hit_distribution[mag][int(data[function][mag][hit]-80)] += 1
                mag_ani_data[mag][genome] = data[function][mag][hit]
util.save("mag_ani_data",mag_ani_data)
util.save("mag_hit_distribution",mag_hit_distribution)
records = []
for mag in mag_hit_distribution:
    if mag not in mag_thresholds:
        mag_thresholds[mag] = {"threshold":0,"threshold_count":0}
    record = {"mag":mag}
    threshold = 0
    for i in range(21):
        record["ani_" + str(80+i)] = mag_hit_distribution[mag][i]
    threshold_count = 0
    for i in range(21):
        index = 20-i  
        if mag_hit_distribution[mag][index] > 0 and (threshold == 0 or threshold == 80+index+1):
            threshold_count += mag_hit_distribution[mag][index]
            threshold = 80+index
    record["threshold"] = threshold
    record["threshold_count"] = threshold_count
    mag_thresholds[mag]["threshold"] = threshold
    mag_thresholds[mag]["threshold_count"] = threshold_count
    records.append(record)
df = pd.DataFrame.from_records(records)
df.to_csv(util.output_dir+"/mag_hit_distribution.csv",index=False)
util.save("mag_thresholds",mag_thresholds)

# Building function profiles based on datafile and threshold

In [20]:
%run cliffcommutil.py
#data = json.load(open('data/annotation_ani_prob_gep_85.json'))
data = json.load(open('/home/fliu/cliff_mags/data/annotation_ani_prob_lo_85.json'))
mag_thresholds = util.load("mag_thresholds")
mag_functions = {}
for function in data.keys():
    for mag in data[function].keys():
        if mag not in mag_functions:
            mag_functions[mag] = {}
        if function not in mag_functions[mag]:
            mag_functions[mag][function] = {"genes":[],"hit_count":0}
        for hit in data[function][mag].keys():
            genome = hit.split(":")[0]
            if genome == "self":
                mag_functions[mag][function]["genes"].append(hit.split(":")[1])
            elif data[function][mag][hit] >= mag_thresholds[mag]["threshold"]:
                mag_functions[mag][function]["hit_count"] += 1/mag_thresholds[mag]["threshold_count"]
                if mag_functions[mag][function]["hit_count"] > 1:
                    mag_functions[mag][function]["hit_count"] = 1
records = []
for mag in mag_functions:
    record = {"mag":mag,"gene_function":0,"functions":len(mag_functions[mag])}
    for i in range(21):
        record["nghitbin_" + str(5*i)] = 0
        record["ghitbin_" + str(5*i)] = 0
    for function in mag_functions[mag]:
        hitbin = int(mag_functions[mag][function]["hit_count"]*100/5)*5
        if len(mag_functions[mag][function]["genes"]) > 0:
            record["gene_function"] += 1
            if hitbin > 0:
                record["ghitbin_" + str(hitbin)] += 1
        else:
            if hitbin > 0:
                record["nghitbin_" + str(hitbin)] += 1
    records.append(record)
df = pd.DataFrame.from_records(records)
df.to_csv(util.output_dir+"/mag_function_distribution.csv",index=False)
util.save("mag_functions",mag_functions)

# Build cliff probabilistic models

In [33]:
%run cliffcommutil.py
mag_functions = util.load("mag_functions")
mag_thresholds = util.load("mag_thresholds")

#Pulling list of already constructed models
done_models = {}
models = util.msrecon.kbase_api.list_objects(174158, object_type="KBaseFBA.FBAModel", include_metadata=False)
for item in models:
    name = item[1][0:-4]
    done_models[name] = item
#Determining the workspace IDs for the mags
mag_wsids = {}
mags = util.msrecon.kbase_api.list_objects(155805, object_type="KBaseGenomes.Genome", include_metadata=False)
for item in mags:
    mag_wsids[item[1]] = item[7]
mags = util.msrecon.kbase_api.list_objects(163264, object_type="KBaseGenomes.Genome", include_metadata=False)
for item in mags:
    mag_wsids[item[1]] = item[7]

#Pulling classifier
genome_classifier = util.msrecon.get_classifier()
util.msrecon.core_template = util.msrecon.get_template(util.msrecon.templates["core"],None)
for mag in mag_functions:
    if mag in done_models:
        print("Done:",mag)
        continue
    if mag in mag_wsids and mag in mag_thresholds and mag_thresholds[mag]["threshold"] > 0:
        print("Working:",mag)
        #Pulling genome
        genome = util.msrecon.get_msgenome(str(mag_wsids[mag])+"/"+mag)
        #Classifying genome
        genome_class = genome_classifier.classify(genome)
        if genome_class == "P":
            genome_class = "Gram Positive"
            template_type = "gp"
        elif genome_class == "N" or genome_class == "--":
            genome_class = "Gram Negative"
            template_type = "gn"
        elif genome_class == "A":
            genome_class = "Archaea"
            template_type = "ar"
        elif genome_class == "C":
            genome_class = "Cyanobacteria"
            template_type = "cyano"
        template = util.msrecon.get_template(util.msrecon.templates[template_type],None)
        #Initializing builder
        builder = MSBuilder(genome, template)
        builder.search_name_to_orginal = {}
        builder.search_name_to_genes = {}
        residual_reaction_gene_hash = {}
        #Processing functions
        function_list = []
        for function in mag_functions[mag]:
            f_norm = normalize_role(function)
            if len(mag_functions[mag][function]["genes"]) > 0:
                for gene in mag_functions[mag][function]["genes"]:
                    if f_norm not in builder.search_name_to_genes:
                        builder.search_name_to_genes[f_norm] = set()
                        builder.search_name_to_orginal[f_norm] = set()
                    builder.search_name_to_orginal[f_norm].add(function)
                    builder.search_name_to_genes[f_norm].add(gene)
            else:
                function_list.append(function)
                fake_gene = "unk."+str(len(function_list))
                if f_norm not in builder.search_name_to_genes:
                    builder.search_name_to_genes[f_norm] = set()
                    builder.search_name_to_orginal[f_norm] = set()
                builder.search_name_to_orginal[f_norm].add(function)
                builder.search_name_to_genes[f_norm].add(fake_gene)
        base_model = FBAModel({'id':mag+".mdl", 'name':genome.scientific_name})
        mdl = builder.build(base_model, '0', False, False)
        #Adding probabilities to reactions
        for reaction in mdl.reactions:
            probability = None
            for gene in reaction.genes:
                if gene.id[0:3] == "unk":
                    i = int(gene.id[4:])-1
                    if mag_functions[mag][function_list[i]]["hit_count"] > 0:
                        if probability == None or probability < mag_functions[mag][function_list[i]]["hit_count"]:
                            probability = mag_functions[mag][function_list[i]]["hit_count"]
                else:
                    probability = 1
            reaction.notes["probability"] = probability
        mdl.genome = genome
        mdl.template = template
        mdl.core_template_ref = str(util.msrecon.core_template.info)
        mdl.genome_ref = str(genome.info)
        mdl.template_ref = str(template.info)
        mdlutl = MSModelUtil.get(mdl)
        atpcorrection = MSATPCorrection(mdlutl,util.msrecon.core_template,[],load_default_medias=True,max_gapfilling=4,gapfilling_delta=1,forced_media=[],default_media_path=util.msrecon.module_dir+"/data/atp_medias.tsv")
        tests = atpcorrection.run_atp_correction()
        mdlutl.get_attributes()["class"] = genome_class
        mdlutl.wsid = mag+".mdl"
        util.msrecon.save_model(mdlutl,174158,None)

/Users/chenry/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:329: UserWarning: Trying to unpickle estimator KNeighborsClassifier from version 1.2.0 when using version 1.0.2. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/modules/model_persistence.html#security-maintainability-limitations
  warnings.warn(


Done: Salt_Pond_MetaG_R1_B_D1_MG_DASTool_bins_concoct_out.59.contigs__.RAST
Done: Salt_Pond_MetaGSF2_B_H2O_MG_DASTool_bins_metabat.28.contigs__.RAST
Done: Salt_Pond_MetaGSF2_A_D2_MG_DASTool_bins_concoct_out.13.contigs__.RAST
Done: Salt_Pond_MetaG_R1_A_D2_MG_DASTool_bins_metabat.48.contigs__.RAST
Done: Salt_Pond_MetaG_R2_restored_C_black_MG_DASTool_bins_concoct_out.17.contigs__.RAST
Done: Salt_Pond_MetaG_R1_A_D2_MG_DASTool_bins_metabat.45.contigs__.RAST
Done: Salt_Pond_MetaGSF2_B_H2O_MG_DASTool_bins_metabat.19.contigs__.RAST
Done: Salt_Pond_MetaG_R2_B_D2_MG_DASTool_bins_metabat.38.contigs__.RAST
Done: Salt_Pond_MetaG_R2A_A_D1_MG_DASTool_bins_concoct_out.42.contigs__.RAST
Done: Salt_Pond_MetaG_R1_C_D1_MG_DASTool_bins_maxbin.047.contigs__.RAST
Done: Salt_Pond_MetaG_R1_C_D1_MG_DASTool_bins_metabat.27.contigs__.RAST
Done: Salt_Pond_MetaGSF2_B_H2O_MG_DASTool_bins_metabat.11.contigs__.RAST
Done: Salt_Pond_MetaG_R2_C_D1_MG_DASTool_bins_concoct_out.65.contigs__.RAST
Done: Salt_Pond_MetaG_R2_C_D

1710512314.380061 INFO: Compartment `e0` sounds like an external compartment. Using this one without counting boundary reactions.
1710512314.409822 INFO: Compartment `e0` sounds like an external compartment. Using this one without counting boundary reactions.
1710512314.442976 INFO: Compartment `e0` sounds like an external compartment. Using this one without counting boundary reactions.
1710512314.477513 INFO: Compartment `e0` sounds like an external compartment. Using this one without counting boundary reactions.
1710512314.511463 INFO: Compartment `e0` sounds like an external compartment. Using this one without counting boundary reactions.
1710512314.54575 INFO: Compartment `e0` sounds like an external compartment. Using this one without counting boundary reactions.
1710512314.5792398 INFO: Compartment `e0` sounds like an external compartment. Using this one without counting boundary reactions.
1710512314.612892 INFO: Compartment `e0` sounds like an external compartment. Using this o

Removing ungapfillable media Etho


1710512318.810345 INFO: Objective with gapfill database:1.0; min objective:0.01
1710512318.875613 INFO: Objective with gapfill database:1.0; min objective:0.01
1710512318.9429069 INFO: Objective with gapfill database:0.33333333333333337; min objective:0.01
1710512319.007444 INFO: Objective with gapfill database:0.0; min objective:0.01
1710512319.732246 WARNING: No gapfilling solution found before filtering for mal-L activating rxn00062_c0
1710512319.7930398 INFO: Objective with gapfill database:2.1249999999999956; min objective:0.01
1710512319.860351 INFO: Objective with gapfill database:0.9999999999999978; min objective:0.01
1710512319.9269729 INFO: Objective with gapfill database:11.874999999999995; min objective:0.01


...

1710516877.158048 INFO: Expansion time:Fum:1.9019707170082256
1710516877.158824 INFO: Filtered count:4 out of 1561


Failed:>rxn05654_c0


1710516878.7536361 INFO: Expansion time:Succ:1.59401698000147
1710516878.754379 INFO: Filtered count:5 out of 1561
1710516879.342994 INFO: Expansion time:Llac:0.5879583279893268
1710516879.3437839 INFO: Filtered count:5 out of 1561
1710516879.904438 INFO: Expansion time:Dlac:0.5599423300009221
1710516879.905173 INFO: Filtered count:5 out of 1561
1710516880.195759 INFO: cpd00075 not found in model!
1710516880.196602 INFO: Media compound: cpd00075 not found in model.
1710516880.444383 INFO: cpd00075 not found in model!
1710516880.44523 INFO: Media compound: cpd00075 not found in model.
1710516880.4575849 INFO: Expansion time:Pyr.NO2:0.5517546129995026
1710516880.4582899 INFO: Filtered count:5 out of 1561
1710516880.9927502 INFO: Expansion time:Pyr.NO3:0.5338483650120907
1710516880.993441 INFO: Filtered count:5 out of 1561
1710516881.518124 INFO: Expansion time:Pyr.NO:0.5240901569923153
1710516881.518847 INFO: Filtered count:5 out of 1561
1710516881.808875 INFO: cpd08021 not found in mode

Failed:>rxn05289_c0


1710516886.4126458 INFO: Expansion time:LLac.SO4.H2:1.680084377003368
1710516886.415264 INFO: Filtered count:6 out of 1561
1710516887.1360042 INFO: Expansion time:LLac.SO4:0.719582879988593
1710516887.1367471 INFO: Filtered count:6 out of 1561
1710516887.137294 INFO: Removing rxn00145_c0 <
1710516887.138227 INFO: Removing rxn05206_c0 >
1710516887.1391768 INFO: Removing rxn23850_c0 <
1710516887.1403651 INFO: Removing rxn00154_c0 <
1710516887.141126 INFO: Removing rxn05654_c0 >
1710516887.142188 INFO: Removing rxn05289_c0 >
1710516888.06119 INFO: cpd00075 not found in model!
1710516888.061913 INFO: Media compound: cpd00075 not found in model.
1710516888.205602 INFO: cpd08021 not found in model!
1710516888.206858 INFO: Media compound: cpd08021 not found in model.
1710516888.254991 INFO: cpd00811 not found in model!
1710516888.255838 INFO: Media compound: cpd00811 not found in model.
1710516888.3057868 INFO: cpd08021 not found in model!
1710516888.3065128 INFO: Media compound: cpd08021 not

# Gapfilling Probabilistic MAG Models

In [ ]:
models = util.msrecon.kbase_api.list_objects(174158, object_type="KBaseFBA.FBAModel", include_metadata=False)
for item in models:
    output = msrecon.gapfill_metabolic_models({
        "workspace":174158,
        "model_list":["151253/GCF_000005845.2.RAST.Complete.mdl"],
        "atp_safe":True,
        "forced_atp_list":[],
        "suffix":".gf",
        "media_list":["KBaseMedia/Carbon-Acetoacetic-Acid","KBaseMedia/Carbon-Mucic-Acid"],
        "templates":None,
        "minimum_objective":0.01,
        "reaction_exlusion_list":[],
        "default_objective":"bio1",
        "save_report_to_kbase":False,
        "gapfilling_mode":"Cumulative",
    })